In [1]:
%matplotlib osx 
import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
from skimage import io
from skimage import img_as_ubyte, img_as_uint, img_as_float64
from skimage.transform import resize, rescale, downscale_local_mean
from skimage.transform import rescale
from PIL import Image

In [2]:

lake = Image.open('USGS_13_n39w124_20200115.tif')
lakearray = np.array(lake)
x1 = lakearray[2300:3412, 9400:10812] ## zooming into crater lake
x1_x = np.shape(lakearray)[0]
x1_y = np.shape(lakearray)[1]


/Users/jamisonlumetta/anaconda3/lib/python3.11/site-packages/PIL/Image.py:3157: DecompressionBombWarning: Image size (116899344 pixels) exceeds limit of 89478485 pixels, could be decompression bomb DOS attack.
  warnings.warn(


10812 10812


In [3]:
NX = 150 #number of rows
NY = 150 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d
LX=NX*dx
LY=NY*dy

Z = resize(x1, (NX, NY))
Z = np.flipud(Z) 

ratio = np.min(Z)/np.min(x1)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
ZMinOrg = np.min(Z)
print(ZMaxOrg)
print(ZMinOrg)

700.89124
61.992134


In [4]:
### Physical Parameters
K = 0.5e-6 # meters^(1-2m)/yr

D = 0.005 # m^2/yr

uplift = .2


In [5]:
### Model parameters

# Time step
# dt = d**2 / D / 8.
dt = d**2 / D /16. #extra small steps
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m= 0.9

#gradient exponent g^n, default n=1
n=0.8

#erosion threshold
theta_c = 10 

 dt[years] =  312.5


In [6]:
# Total simulation time
T = 250000

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of iterations: ',n_iter)

Number of iterations:  800


In [7]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.1  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))


Minimum elevation           61.992134
Maximum elevation           700.89124
Beach level                 125.88204498291016
Ocean volume                13658.234420776538
Percentage of ocean surface 3.0666666666666664


In [8]:
 # Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
    plt.clf()
    ax1 = fig.add_subplot(121,projection='3d')
    
    # use equal x-y aspect with an explicit vertical exageration
    vert_exag = 0
    ax1.set_ylim3d(0,NX)
    ax1.set_xlim3d(0,NY)
    ax1.set_zlim3d(0,(ZMaxOrg-ZMinOrg)/ratio + 700)
    ax1.set_zlabel('meters')
    

    ax1.set_title('Surface Relief')
    
    #        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
    #                antialiased=False,linewidth=0)
    
    ZPlot = np.copy(Z/ratio)
    ZPlot[ZPlot<ls.ZBeachLevel/ratio] = ls.ZBeachLevel/ratio 
    ZPlot -= ls.ZBeachLevel/ratio
    ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,antialiased=False,linewidth=0)
    
    ax2 = fig.add_subplot(122,aspect='equal')
    ax2.set_title('Elevation')
    
    #im = ax2.pcolor(Z,cmap=cm.terrain)
    im = ax2.pcolor(ZPlot,cmap=cm.terrain)
    cs = ax2.contour(ZPlot,6,colors='k')

    # Add a color bar which maps values to colors.
    cbar = fig.colorbar(im, shrink=0.5, aspect=5)
    # Add the contour line levels to the colorbar
    cbar.add_lines(cs)
    cbar.ax.set_ylabel('meters')
    
    #plt.show()
    plt.draw()
    plt.pause(0.001)

In [9]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='animationsonoma250ky2up.mp4', artist='Matplotlib',comment='500k yr sim')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)


# Set up figure
fig = init_figure()
# update_figure()
Znew = np.copy(Z)


with writer.saving(fig, "animationsonoma250ky2up.mp4", dpi=200):
    nf = n_iter + 1
    for it in range(1,nf):
        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero
    
            #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)


        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            writer.grab_frame()

        else:
             print('.',end='')

    update_figure()
    writer.grab_frame()
print(' Simulation finished.')

.........10.........20.........30.........40.........50.........60.........70.........80.........90.........100.........110.........120.........130.........140.........150.........160.........170.........180.........190.........200.........210.........220.........230.........240.........250.........260.........270.........280.........290.........300.........310.........320.........330.........340.........350.........360.........370.........380.........390.........400.........410.........420.........430.........440.........450.........460.........470.........480.........490.........500.........510.........520.........530.........540.........550.........560.........570.........580.........590.........600.........610.........620.........630.........640.........650.........660.........670.........680.........690.........700.........710.........720.........730.........740.........750.........760.........770.........780.........790.........800 Simulation finished.
